先爬取所有老师信息

In [13]:
import requests
from bs4 import BeautifulSoup
import re
import time
import json

headers = {'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome / 78.0.3904.108Safari / 537.36'}

try:
    url = [
        'http://finance.jxufe.edu.cn/news-list-fujiaoshou.html', 
        'http://finance.jxufe.edu.cn/news-list-fujiaoshou-2.html',
    ]
    
    opts = [
        '姓　　名', '姓　名', '姓　别', '性　　别', '政治面貌', '毕业院校', '毕业专业', '职　　称',
    ]

    dic = {}
    
    for chose in url:
        r = requests.get(chose, headers=headers)
        soup = BeautifulSoup(r.text, 'lxml')
    #     print(soup)
        pattern = soup.find_all('div', class_='textlist')



        for item in pattern:
    #         pattern_re = re.compile('<div class="textlist"> <a href=".*?">')
    #         print(type(item))
            name = item.a.get_text()
            href = item.a.get("href")

            url_in = href
            r_in = requests.get(url_in, headers=headers)
            soup_in = BeautifulSoup(r_in.text, 'lxml')

            pattern_in = soup_in.find_all('div', class_='ne_main_R')
            
            name = ''
            dic_in = {}
            article = ''
            
            for div in pattern_in:
                div_set = div.find_all('p')
                for i in div_set:
                    para = i.get_text()
                    article += para + '\n'
                    for op in opts:
                        method = re.compile('(?<=\\' + op + '：' + ').+')
                        res = re.findall(method, para)
                        if res != []:
                            if op == opts[0] or op == opts[1]:
                                name = res[0]
#                             print(op + ': ' + res[0])
                            dic_in[op] = res[0]
    
#                 print(article)
            dic[name] = dic_in
            dic[name]['基本信息'] = article
            dic_in = {}
        
    
        time.sleep(1)
    
    datajson = json.dumps(dic, sort_keys=True, indent=4, ensure_ascii=False)
    
    print(datajson)
    
    with open('jsondata.json','w',encoding='utf-8') as file:
        file.write(json.dumps(dic, indent=2, ensure_ascii=False))
    
    
except TimeoutError:
    print('Request Time out')


{
    "": {
        "基本信息": "\nå§ããåï¼è°­è±è´¤\næ§ããå«ï¼ç·\nåºçå¹´æï¼\næ¿æ²»é¢è²ï¼ä¸­å±åå\næ¯ä¸é¢æ ¡ï¼æ¹åå¤§å­¦\næ¯ä¸ä¸ä¸ï¼éèå­¦\nèããç§°ï¼å¯ææ/ç ç©¶çå¯¼å¸\né®        ç®±ï¼yxtan6@163.com\n\n \nä¸ãåºæ¬æåµ\nè°­è±è´¤ï¼ç·ï¼åå£«ãå¯ææãä¸­å½åç²¾ç®å¸ãç®åæ¯ä¸­å½ç²¾ç®å¸åä¼ä¼åï¼ä¸æµ·è´¢ç»å¤§å­¦åå£«åãç ç©¶æ¹åä¸ºå¬å¸éèãèµäº§å®ä»·ä¸éèç§æç­ï¼ä»¥ç¬¬ä¸ä½èèº«ä»½å¨International Review of Economics & Financeï¼ North American Journal of Economics and Financ eï¼Finance Research Lettersç­å½ééè¦SSCIæååãä¸­å½ç®¡çç§å­¦ãç­å½åéè¦æååè¡¨å­¦æ¯è®ºæå¤ç¯ï¼æ¾å¤æ¬¡åå å½åå¤é«æ°´å¹³çå­¦æ¯ä¼è®®ãç®åä¸»æå½å®¶èªç§åºééå¹´é¡¹ç®ãæè²é¨äººæç¤¾ç§åºéãåå£«åé¢ä¸åºéä»¥åçç¤¾ç§è§åé¡¹ç®å¤é¡¹ã\n\näºãå¼è®¾è¯¾ç¨ \næ¬ç§çè¯¾ç¨ï¼éèç»æµå­¦ï¼éèå·¥ç¨ï¼ä¿é©ç²¾ç®ï¼\nç ç©¶ç

启示：副教授信息没有统一标准的格式，所以采取上述方法并不能很好地将老师信息归于同一张表，故我使用了json格式进行归类，通过py文件进行。